In [2]:
import pandas as pd
import numpy as np
from scipy.stats import iqr

from ppc_db import sql_extractdata

db_args = {
    'user':'root',
    'password':'password',
    'host':'localhost',
    'port':3306,
    'database':'CSV_DB 7'
 }

In [22]:
cols = ['7_county', 'price_gbp']

query = f"SELECT {", ".join(str(x) for x in cols)} FROM Oct24pricepaidcomplete WHERE YEAR(date)=2023"
result = pd.DataFrame(sql_extractdata(query, **db_args),columns=cols)

df = (result.join
      (pd.read_csv('county_to_region.csv',
                   index_col='7_county',
                   dtype=str),
                   on='7_county')
     )

In [23]:
import plotly.express as px
fig = px.histogram(df, x="price_gbp",color='region',nbins=2000)
fig.update_layout(xaxis_range=[0,1e6],barmode='overlay')
fig.show()

In [24]:
import plotly.graph_objects as go

df_by_region = df.groupby('region')['price_gbp']


fig = px.bar(df.groupby('region')['price_gbp'].median())
fig = go.Figure(
    data=[
        go.Bar(
            x=df_by_region.median().index,
            y=df_by_region.median().values,
            name="Median",
            marker=dict(color="paleturquoise"),
        ),
    go.Bar(
        x=df_by_region.agg(iqr).index,
        y=df_by_region.agg(iqr).values,
        name="IQR",
        marker=dict(color="crimson"),
    )
    ]
)

fig.update_layout(
    legend=dict(orientation="v"),
    yaxis=dict(
        title=dict(text="Median, GBP"),
        side="left",
    ),
    yaxis2=dict(
        title=dict(text="Skew"),
        side="right",
        overlaying="y",
        tickmode="sync",
    ),
    barmode='group'
)

fig.show()

In [37]:
cols = ['YEAR(date)', '7_county', 'COUNT(`tx_id`)']

query = f"SELECT {", ".join(str(x) for x in cols)} FROM Oct24pricepaidcomplete WHERE MONTH(date) < 4 GROUP BY YEAR(date), 7_county"
result = pd.DataFrame(sql_extractdata(query, **db_args),columns=cols)

df = (result.join
      (pd.read_csv('county_to_region.csv',
                   index_col='7_county',
                   dtype=str),
                   on='7_county')
     )

df_midyr = df.groupby(['YEAR(date)','region']).sum().drop('7_county',axis=1).unstack()['COUNT(`tx_id`)']
df_midyr = df_midyr[df_midyr.index>2007].apply(lambda x:x/x.iloc[0])

In [39]:
df_midyr

region      East Midlands  East of England    London  North East  North West  \
YEAR(date)                                                                     
2008             1.000000         1.000000  1.000000    1.000000    1.000000   
2009             0.518570         0.538153  0.420263    0.468092    0.460180   
2010             0.704535         0.785750  0.781234    0.556348    0.601126   
2011             0.663092         0.754807  0.721982    0.579090    0.593463   
2012             0.798544         0.929501  0.875570    0.648789    0.670562   
2013             0.767627         0.865311  0.829883    0.623671    0.663280   
2014             1.170871         1.267474  1.191089    0.944558    1.019518   
2015             1.097319         1.174645  1.068686    0.920457    1.007325   
2016             1.612512         1.671090  1.541379    1.210342    1.453872   
2017             1.335386         1.322952  1.088060    1.173795    1.284093   
2018             1.332142         1.257360  0.992593    1.126952    1.265295   
2019             1.293678         1.192970  0.940943    1.181828    1.277531   
2020             1.227011         1.197677  0.996414    1.125820    1.237859   
2021             1.868123         2.091678  1.594316    1.596176    1.763961   
2022             1.414101         1.360154  1.062995    1.356302    1.385325   
2023             1.139623         1.076357  0.901571    1.183413    1.149117   
2024             0.823568         0.773533  0.661560    0.893075    0.853338   

region      South East  South West     Wales  West Midlands  \
YEAR(date)                                                    
2008          1.000000    1.000000  1.000000       1.000000   
2009          0.550236    0.597429  0.546994       0.509623   
2010          0.795565    0.810061  0.701097       0.659758   
2011          0.740930    0.758077  0.706465       0.653220   
2012          0.920289    0.969033  0.775406       0.794288   
2013          0.852407    0.877641  0.773736       0.761658   
2014          1.250832    1.306149  1.138120       1.121823   
2015          1.161696    1.215260  1.116889       1.096965   
2016          1.642370    1.821017  1.554389       1.581359   
2017          1.271790    1.471157  1.421875       1.361769   
2018          1.208192    1.385075  1.441913       1.359425   
2019          1.125647    1.340190  1.399094       1.335862   
2020          1.148614    1.300950  1.395992       1.255551   
2021          2.073055    2.191392  1.789003       1.891377   
2022          1.314166    1.443712  1.556536       1.400259   
2023          1.047352    1.200112  1.229246       1.158771   
2024          0.777606    0.883287  0.921279       0.871762   

region      Yorkshire and the Humber  
YEAR(date)                            
2008                        1.000000  
2009                        0.496815  
2010                        0.616974  
2011                        0.591381  
2012                        0.706490  
2013                        0.700407  
2014                        1.042061  
2015                        0.985195  
2016                        1.391175  
2017                        1.275090  
2018                        1.231308  
2019                        1.263499  
2020                        1.166351  
2021                        1.738854  
2022                        1.325931  
2023                        1.120560  
2024                        0.841338

In [34]:
cols = ['YEAR(date)', '7_county', 'COUNT(`tx_id`)']

query = f"SELECT {", ".join(str(x) for x in cols)} FROM Oct24pricepaidcomplete GROUP BY YEAR(date), 7_county"
result = pd.DataFrame(sql_extractdata(query, **db_args),columns=cols)

df = (result.join
      (pd.read_csv('county_to_region.csv',
                   index_col='7_county',
                   dtype=str),
                   on='7_county')
     )

df_fullyear = df.groupby(['YEAR(date)','region']).sum().drop('7_county',axis=1).unstack()['COUNT(`tx_id`)']
df_fullyear = df_fullyear[df_fullyear.index>2007].apply(lambda x:x/x.iloc[0])

In [35]:
df_fullyear = df_fullyear[df_fullyear.index<2024]

In [36]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(rows=5,cols=2,subplot_titles=df_midyr.columns)

for index,value in enumerate(df_midyr.columns):
    row = [1,1,2,2,3,3,4,4,5,5]
    col = [1,2,1,2,1,2,1,2,1,2]
    fig.add_trace(go.Scatter(x=df_fullyear[value].index,y=df_fullyear[value].values),row=row[index],col=col[index])

fig.update_layout(height=1000, width=800, showlegend=False,
                  title_text="Number of Transactions by Year, Full Year")

fig.show()

In [40]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(rows=5,cols=2,subplot_titles=df_midyr.columns)

for index,value in enumerate(df_midyr.columns):
    row = [1,1,2,2,3,3,4,4,5,5]
    col = [1,2,1,2,1,2,1,2,1,2]
    fig.add_trace(go.Scatter(x=df_midyr[value].index,y=df_midyr[value].values),row=row[index],col=col[index])

fig.update_layout(height=1000, width=800, showlegend=False,
                  title_text="Number of Transactions by Year, 1Q")

fig.show()

In [18]:
import datetime

cols = ['MONTH(date)','YEAR(date)', '7_county', 'COUNT(`tx_id`)']

query = f"SELECT {", ".join(str(x) for x in cols)} FROM Oct24pricepaidcomplete WHERE MONTH(date) < 4 GROUP BY MONTH(date),YEAR(date), 7_county"
result = pd.DataFrame(sql_extractdata(query, **db_args),columns=cols)

df = (result.join
      (pd.read_csv('county_to_region.csv',
                   index_col='7_county',
                   dtype=str),
                   on='7_county')
     )

df = df[df['YEAR(date)'].isin([2007,2008,2009,2010,2014,2023,2024])]
df['date']=df.apply(lambda x: datetime.datetime(x['YEAR(date)'],x['MONTH(date)'],1),axis=1)
df = df.groupby(['date','region']).sum().drop('7_county',axis=1).unstack()['COUNT(`tx_id`)']


In [11]:
fig = px.line(x=df.index.month,y=df['London'], color=df.index.year)
fig.show()

In [20]:
range_list = [str(i)+"-"+str(i+249999) for i in range(0,3500000,250000)]
cols=['Year','7_county',*range_list]

count_strings = ["count(case when `price_gbp` between "+str(i) +" and "+ str(i+249999) +" then 1 end) `bucket("+str(i)+"-"+str(i+249999)+"`" for i in range(0,3500000,250000)]

sql_cols = ['YEAR(date)', '7_county']+count_strings

query = f"SELECT {", ".join(str(x) for x in sql_cols)} FROM Oct24pricepaidcomplete WHERE MONTH(date) < 4 GROUP BY YEAR(date), 7_county"
result = pd.DataFrame(sql_extractdata(query, **db_args),columns=cols)

df = (result.join
      (pd.read_csv('county_to_region.csv',
                   index_col='7_county',
                   dtype=str),
                   on='7_county')
     )


In [13]:
df.drop('7_county',axis=1,inplace=True)

In [14]:
df_Lon = df.loc[df.region=='London'].drop('region',axis=1).set_index('Year')
df_SE = df.loc[df.region=='South East'].drop('region',axis=1).set_index('Year')
df_SE = df_SE.groupby(df_SE.index).sum()

In [15]:
fig = px.line(df_Lon[df_Lon.index>2018].apply(lambda x:x/x.iloc[0]).transpose())
fig.show()

In [16]:
fig = px.line(df_SE[df_SE.index>2018].apply(lambda x:x/x.iloc[0]).transpose())
fig.show()